# Vector calculus with SageMath

## 3. Using cylindrical coordinates

This notebook illustrates operations on vector fields on Euclidean spaces, as introduced in Trac ticket [#24623](https://trac.sagemath.org/ticket/24623).

In [1]:
version()

'SageMath version 8.2.rc4, Release Date: 2018-04-20'

In [2]:
%display latex

In [3]:
from sage.manifolds.operators import *   # to get the operators grad, div, curl, etc.

## The 3-dimensional Euclidean space

We start by declaring the 3-dimensional Euclidean space $\mathbb{E}^3$, with $(\rho,\phi,z)$ as spherical coordinates:

In [4]:
E.<rh,ph,z> = EuclideanSpace(coordinates='cylindrical')
print(E)
E

Euclidean space E^3


Euclidean space E^3

$\mathbb{E}^3$ is endowed with the chart of cylindrical coordinates:

In [5]:
E.atlas()

[Chart (E^3, (rh, ph, z))]

as well as with the associated orthonormal vector frame $(e_\rho, e_\phi, e_z)$:

In [6]:
E.frames()

[Coordinate frame (E^3, (d/drh,d/dph,d/dz)),
 Vector frame (E^3, (e_rh,e_ph,e_z))]

In the above output, $\left(\frac{\partial}{\partial\rho}, \frac{\partial}{\partial\phi}, \frac{\partial}{\partial z}\right)$ is the coordinate frame associated with $(\rho,\phi,z)$; it is not an orthonormal frame and will not be used below.

## Vector fields

We define a vector field on $\mathbb{E}^3$ from its components in the orthonormal vector frame $(e_\rho,e_\phi,e_z)$:

In [7]:
v = E.vector_field(rh*(1+sin(2*ph)), 2*rh*cos(ph)^2, z,
                   name='v')
v.display()

v = rh*(sin(2*ph) + 1) e_rh + 2*rh*cos(ph)^2 e_ph + z e_z

We can access to the components of $v$ via the square bracket operator:

In [8]:
v[1]

rh*(sin(2*ph) + 1)

In [9]:
v[:]

[rh*(sin(2*ph) + 1), 2*rh*cos(ph)^2, z]

A vector field can evaluated at any point of $\mathbb{E}^3$:

In [10]:
p = E((1, pi, 0), name='p')
print(p)

Point p on the Euclidean space E^3


In [11]:
p.coordinates()

(1, pi, 0)

In [12]:
vp = v.at(p)
print(vp)

Vector v at Point p on the Euclidean space E^3


In [13]:
vp.display()

v = e_rh + 2 e_ph

We may define a vector field with generic components:

In [14]:
u = E.vector_field(function('u_rho')(rh,ph,z),
                   function('u_phi')(rh,ph,z),
                   function('u_z')(rh,ph,z),
                   name='u')
u.display()

u = u_rho(rh, ph, z) e_rh + u_phi(rh, ph, z) e_ph + u_z(rh, ph, z) e_z

In [15]:
u[:]

[u_rho(rh, ph, z), u_phi(rh, ph, z), u_z(rh, ph, z)]

In [16]:
up = u.at(p)
up.display()

u = u_rho(1, pi, 0) e_rh + u_phi(1, pi, 0) e_ph + u_z(1, pi, 0) e_z

## Algebraic operations on vector fields

### Dot product

The dot (or scalar) product of the vector fields $u$ and $v$ is obtained by the method `dot_product`, which admits `dot` as a shortcut alias:

In [17]:
s = u.dot(v)
s

Scalar field u.v on the Euclidean space E^3

In [18]:
print(s)

Scalar field u.v on the Euclidean space E^3


$s= u\cdot v$ is a *scalar field*, i.e. a map $\mathbb{E}^3 \rightarrow \mathbb{R}$:

In [19]:
s.display()

u.v: E^3 --> R
   (rh, ph, z) |--> 2*rh*cos(ph)^2*u_phi(rh, ph, z) + (2*cos(ph)*sin(ph) + 1)*rh*u_rho(rh, ph, z) + z*u_z(rh, ph, z)

It maps point of $\mathbb{E}^3$ to real numbers:

In [20]:
s(p)

2*u_phi(1, pi, 0) + u_rho(1, pi, 0)

Its coordinate expression is

In [21]:
s.expr()

2*rh*cos(ph)^2*u_phi(rh, ph, z) + (2*cos(ph)*sin(ph) + 1)*rh*u_rho(rh, ph, z) + z*u_z(rh, ph, z)

### Norm

The norm of a vector field is 

In [22]:
s = norm(u)
s

Scalar field |u| on the Euclidean space E^3

In [23]:
s.display()

|u|: E^3 --> R
   (rh, ph, z) |--> sqrt(u_phi(rh, ph, z)^2 + u_rho(rh, ph, z)^2 + u_z(rh, ph, z)^2)

In [24]:
s.expr()

sqrt(u_phi(rh, ph, z)^2 + u_rho(rh, ph, z)^2 + u_z(rh, ph, z)^2)

The norm is related to the dot product by $\|u\|^2 = u\cdot u$, as we can check:

In [25]:
norm(u)^2 == u.dot(u)

True

For $v$, we have:

In [26]:
norm(v).expr()

sqrt((4*cos(ph)^2 + 4*cos(ph)*sin(ph) + 1)*rh^2 + z^2)

### Cross product

The cross product of $u$ by $v$ is obtained by the method `cross_product`, which admits `cross` as a shortcut alias:

In [27]:
s = u.cross(v)
print(s)

Vector field u x v on the Euclidean space E^3


In [28]:
s.display()

u x v = (-2*rh*cos(ph)^2*u_z(rh, ph, z) + z*u_phi(rh, ph, z)) e_rh + ((2*cos(ph)*sin(ph) + 1)*rh*u_z(rh, ph, z) - z*u_rho(rh, ph, z)) e_ph + (2*rh*cos(ph)^2*u_rho(rh, ph, z) - (2*cos(ph)*sin(ph) + 1)*rh*u_phi(rh, ph, z)) e_z

### Scalar triple product

Let us introduce a third vector field. As a example, we do not pass the components as arguments of `vector_field`, as we did for $u$ and $v$; instead, we set them in a second stage, via the square bracket operator, any unset component being assumed to be zero:

In [29]:
w = E.vector_field(name='w')
w[1] = rh
w[3] = z
w.display()

w = rh e_rh + z e_z

The scalar triple product of the vector fields $u$, $v$ and $w$ is obtained as follows: 

In [30]:
triple_product = E.scalar_triple_product()
s = triple_product(u, v, w)
print(s)

Scalar field epsilon(u,v,w) on the Euclidean space E^3


In [31]:
s.expr()

-2*rh^2*cos(ph)^2*u_z(rh, ph, z) - 2*(rh*cos(ph)*sin(ph)*u_phi(rh, ph, z) - rh*cos(ph)^2*u_rho(rh, ph, z))*z

Let us check that the scalar triple product of $u$, $v$ and $w$ is $u\cdot(v\times w)$:

In [32]:
s == u.dot(v.cross(w))

True

## Differential operators

### Gradient of a scalar field

We first introduce a scalar field, via its expression in terms of Cartesian coordinates; in this example, we consider a unspecified function of $(\rho,\phi,z)$:

In [33]:
F = E.scalar_field(function('f')(rh,ph,z), name='F')
F.display()

F: E^3 --> R
   (rh, ph, z) |--> f(rh, ph, z)

The value of $F$ at a point:

In [34]:
F(p)

f(1, pi, 0)

The gradient of $F$:

In [35]:
print(grad(F))

Vector field grad(F) on the Euclidean space E^3


In [36]:
grad(F).display()

grad(F) = d(f)/drh e_rh + d(f)/dph/rh e_ph + d(f)/dz e_z

In [37]:
norm(grad(F)).display()

|grad(F)|: E^3 --> R
   (rh, ph, z) |--> sqrt(rh^2*(d(f)/drh)^2 + rh^2*(d(f)/dz)^2 + (d(f)/dph)^2)/rh

### Divergence 

The divergence of a vector field:

In [38]:
s = div(u)
s.display()

div(u): E^3 --> R
   (rh, ph, z) |--> (rh*d(u_rho)/drh + rh*d(u_z)/dz + u_rho(rh, ph, z) + d(u_phi)/dph)/rh

In [39]:
s.expr().expand()

u_rho(rh, ph, z)/rh + diff(u_phi(rh, ph, z), ph)/rh + diff(u_rho(rh, ph, z), rh) + diff(u_z(rh, ph, z), z)

For $v$ and $w$, we have

In [40]:
div(v).expr()

3

In [41]:
div(w).expr()

3

An identity valid for any scalar field $F$ and any vector field $u$:

In [42]:
div(F*u) == F*div(u) + u.dot(grad(F))

True

### Curl

The curl of a vector field:

In [43]:
s = curl(u)
print(s)

Vector field curl(u) on the Euclidean space E^3


In [44]:
s.display()

curl(u) = -(rh*d(u_phi)/dz - d(u_z)/dph)/rh e_rh + (d(u_rho)/dz - d(u_z)/drh) e_ph + (rh*d(u_phi)/drh + u_phi(rh, ph, z) - d(u_rho)/dph)/rh e_z

To use the notation `rot` instead of  `curl`, simply do

In [45]:
rot = curl

An alternative is

In [46]:
from sage.manifolds.operators import curl as rot

We have then

In [47]:
rot(u).display()

curl(u) = -(rh*d(u_phi)/dz - d(u_z)/dph)/rh e_rh + (d(u_rho)/dz - d(u_z)/drh) e_ph + (rh*d(u_phi)/drh + u_phi(rh, ph, z) - d(u_rho)/dph)/rh e_z

In [48]:
rot(u) == curl(u)

True

For $v$ and $w$, we have:

In [49]:
curl(v).display()

curl(v) = 2 e_z

In [50]:
curl(w).display()

curl(w) = 0

The curl of a gradient is always zero:

In [51]:
curl(grad(F)).display()

curl(grad(F)) = 0

The divergence of a curl is always zero:

In [52]:
div(curl(u)).display()

div(curl(u)): E^3 --> R
   (rh, ph, z) |--> 0

An identity valid for any scalar field $F$ and any vector field $u$:

In [53]:
curl(F*u) == grad(F).cross(u) + F*curl(u)

True

### Laplacian

The Laplacian of a scalar field:

In [54]:
s = laplacian(F)
s.display()

Delta(F): E^3 --> R
   (rh, ph, z) |--> (rh^2*d^2(f)/drh^2 + rh^2*d^2(f)/dz^2 + rh*d(f)/drh + d^2(f)/dph^2)/rh^2

In [55]:
s.expr().expand()

diff(f(rh, ph, z), rh)/rh + diff(f(rh, ph, z), ph, ph)/rh^2 + diff(f(rh, ph, z), rh, rh) + diff(f(rh, ph, z), z, z)

For a scalar field, the Laplacian is nothing but the divergence of the gradient:

In [56]:
laplacian(F) == div(grad(F))

True

The Laplacian of a vector field:

In [57]:
Du = laplacian(u)
Du.display()

Delta(u) = (rh^2*d^2(u_rho)/drh^2 + rh^2*d^2(u_rho)/dz^2 + rh*d(u_rho)/drh - u_rho(rh, ph, z) - 2*d(u_phi)/dph + d^2(u_rho)/dph^2)/rh^2 e_rh + (rh^2*d^2(u_phi)/drh^2 + rh^2*d^2(u_phi)/dz^2 + rh*d(u_phi)/drh - u_phi(rh, ph, z) + d^2(u_phi)/dph^2 + 2*d(u_rho)/dph)/rh^2 e_ph + (rh^2*d^2(u_z)/drh^2 + rh^2*d^2(u_z)/dz^2 + rh*d(u_z)/drh + d^2(u_z)/dph^2)/rh^2 e_z

Since this expression is quite lengthy, we may ask for a display component by component:

In [58]:
Du.display_comp()

Delta(u)^1 = (rh^2*d^2(u_rho)/drh^2 + rh^2*d^2(u_rho)/dz^2 + rh*d(u_rho)/drh - u_rho(rh, ph, z) - 2*d(u_phi)/dph + d^2(u_rho)/dph^2)/rh^2 
Delta(u)^2 = (rh^2*d^2(u_phi)/drh^2 + rh^2*d^2(u_phi)/dz^2 + rh*d(u_phi)/drh - u_phi(rh, ph, z) + d^2(u_phi)/dph^2 + 2*d(u_rho)/dph)/rh^2 
Delta(u)^3 = (rh^2*d^2(u_z)/drh^2 + rh^2*d^2(u_z)/dz^2 + rh*d(u_z)/drh + d^2(u_z)/dph^2)/rh^2

We may expand each component:

In [59]:
for i in E.irange():
    Du[i].expand()
Du.display_comp()

Delta(u)^1 = d(u_rho)/drh/rh - u_rho(rh, ph, z)/rh^2 - 2*d(u_phi)/dph/rh^2 + d^2(u_rho)/dph^2/rh^2 + d^2(u_rho)/drh^2 + d^2(u_rho)/dz^2 
Delta(u)^2 = d(u_phi)/drh/rh - u_phi(rh, ph, z)/rh^2 + d^2(u_phi)/dph^2/rh^2 + 2*d(u_rho)/dph/rh^2 + d^2(u_phi)/drh^2 + d^2(u_phi)/dz^2 
Delta(u)^3 = d(u_z)/drh/rh + d^2(u_z)/dph^2/rh^2 + d^2(u_z)/drh^2 + d^2(u_z)/dz^2

In [60]:
Du[1]

d(u_rho)/drh/rh - u_rho(rh, ph, z)/rh^2 - 2*d(u_phi)/dph/rh^2 + d^2(u_rho)/dph^2/rh^2 + d^2(u_rho)/drh^2 + d^2(u_rho)/dz^2

In [61]:
Du[2]

d(u_phi)/drh/rh - u_phi(rh, ph, z)/rh^2 + d^2(u_phi)/dph^2/rh^2 + 2*d(u_rho)/dph/rh^2 + d^2(u_phi)/drh^2 + d^2(u_phi)/dz^2

In [62]:
Du[3]

d(u_z)/drh/rh + d^2(u_z)/dph^2/rh^2 + d^2(u_z)/drh^2 + d^2(u_z)/dz^2

As a test, we may check that these formulas coincide with those of
Wikipedia's article [*Del in cylindrical and spherical coordinates*](https://en.wikipedia.org/wiki/Del_in_cylindrical_and_spherical_coordinates#Del_formula).

For $v$ and $w$, we have 

In [63]:
laplacian(v).display()

Delta(v) = 0

In [64]:
laplacian(w).display()

Delta(w) = 0

We have:

In [65]:
curl(curl(u)).display()

curl(curl(u)) = -(rh^2*d^2(u_rho)/dz^2 - rh^2*d^2(u_z)/drhdz - rh*d^2(u_phi)/drhdph - d(u_phi)/dph + d^2(u_rho)/dph^2)/rh^2 e_rh - (rh^2*d^2(u_phi)/drh^2 + rh^2*d^2(u_phi)/dz^2 + rh*d(u_phi)/drh - rh*d^2(u_rho)/drhdph - rh*d^2(u_z)/dphdz - u_phi(rh, ph, z) + d(u_rho)/dph)/rh^2 e_ph + (rh^2*d^2(u_rho)/drhdz - rh^2*d^2(u_z)/drh^2 + rh*d^2(u_phi)/dphdz + rh*d(u_rho)/dz - rh*d(u_z)/drh - d^2(u_z)/dph^2)/rh^2 e_z

In [66]:
grad(div(u)).display()

grad(div(u)) = (rh^2*d^2(u_rho)/drh^2 + rh^2*d^2(u_z)/drhdz + rh*d^2(u_phi)/drhdph + rh*d(u_rho)/drh - u_rho(rh, ph, z) - d(u_phi)/dph)/rh^2 e_rh + (rh*d^2(u_rho)/drhdph + rh*d^2(u_z)/dphdz + d^2(u_phi)/dph^2 + d(u_rho)/dph)/rh^2 e_ph + (rh*d^2(u_rho)/drhdz + rh*d^2(u_z)/dz^2 + d^2(u_phi)/dphdz + d(u_rho)/dz)/rh e_z

and we may check a famous identity:

In [67]:
curl(curl(u)) == grad(div(u)) - laplacian(u)

True

## Customizations

### Customizing the symbols of the orthonormal frame vectors

By default, the vectors of the orthonormal frame associated with cylindrical coordinates are denoted $(e_\rho,e_\phi,z)$:

In [68]:
frame = E.cylindrical_frame()
frame

Vector frame (E^3, (e_rh,e_ph,e_z))

But this can be changed, thanks to the method `set_name`:

In [69]:
frame.set_name('a', indices=('rh', 'ph', 'z'),
               latex_indices=(r'\rho', r'\phi', 'z'))
frame

Vector frame (E^3, (a_rh,a_ph,a_z))

In [70]:
v.display()

v = rh*(sin(2*ph) + 1) a_rh + 2*rh*cos(ph)^2 a_ph + z a_z

In [71]:
frame.set_name(('hrh', 'hph', 'hz'), 
               latex_symbol=(r'\hat{\rho}', r'\hat{\phi}', r'\hat{z}'))
frame

Vector frame (E^3, (hrh,hph,hz))

In [72]:
v.display()

v = rh*(sin(2*ph) + 1) hrh + 2*rh*cos(ph)^2 hph + z hz

### Customizing the coordinate symbols

The coordinates symbols are defined within the angle brackets `<...>` at the construction of the Euclidean space. Above we did 

In [73]:
E.<rh,ph,z> = EuclideanSpace(coordinates='cylindrical')

which resulted in the coordinate symbols $(\rho,\phi,z)$ and in the corresponding Python variables `rh`, `ph` and `z` (SageMath symbolic expressions). Using other symbols, for instance $(R,\Phi,Z)$, is possible through the optional argument `symbols` of the function `EuclideanSpace`. It has to be a string, usually prefixed by r (for raw string, in order to allow for the backslash character of LaTeX expressions). This string contains the coordinate fields separated by a blank space; each field contains the coordinate’s text symbol and possibly the coordinate’s LaTeX symbol (when the latter is different from the text symbol), both symbols being separated by a colon (`:`):

In [74]:
E.<R,Ph,Z> = EuclideanSpace(coordinates='cylindrical', symbols=r'R Ph:\Phi Z')

We have then

In [75]:
E.atlas()

[Chart (E^3, (R, Ph, Z))]

In [76]:
E.frames()

[Coordinate frame (E^3, (d/dR,d/dPh,d/dZ)), Vector frame (E^3, (e_R,e_Ph,e_Z))]

In [77]:
E.cylindrical_frame()

Vector frame (E^3, (e_R,e_Ph,e_Z))

In [78]:
v = E.vector_field(R*(1+sin(2*Ph)), 2*R*cos(Ph)^2, Z,
                   name='v')
v.display()

v = R*(sin(2*Ph) + 1) e_R + 2*R*cos(Ph)^2 e_Ph + Z e_Z